# Book recommendation system: Content-based solution

In [1]:
# importing standard Python libraries for data analysis
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import datetime as dt

In [2]:
# importing Python libraries for machine learning
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler
from sklearn.metrics.pairwise import cosine_similarity

In [3]:
# I would like to see all rows and columns of dataframes
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# do not show warnings
import warnings
warnings.filterwarnings('ignore')

In [4]:
# looking at final dataset from previous data wrangling part of the project
final = pd.read_csv('final.csv', sep=',')
final.head()

Unnamed: 0  user   age country_2        isbn  rating  rating_count  \
0           0     9   NaN       usa  0452264464       6            79   
1           1  3373  30.0       usa  0452264464      10            79   
2           2  5555   NaN    france  0452264464       9            79   
3           3  6242   NaN    canada  0452264464       5            79   
4           4  8570  23.0       usa  0452264464       8            79   

   avg_rating  reaction_index                                 title  \
0    7.772152        0.438889  beloved (plume contemporary fiction)   
1    7.772152        0.438889  beloved (plume contemporary fiction)   
2    7.772152        0.438889  beloved (plume contemporary fiction)   
3    7.772152        0.438889  beloved (plume contemporary fiction)   
4    7.772152        0.438889  beloved (plume contemporary fiction)   

          author  median_age_raters title_api  \
0  toni morrison               34.0   beloved   
1  toni morrison               34.0   beloved   
2  toni morrison               34.0   beloved   
3  toni morrison               34.0   beloved   
4  toni morrison               34.0   beloved   

                                         description category  pages  
0  Staring unflinchingly into the abyss of slaver...  fiction    275  
1  Staring unflinchingly into the abyss of slaver...  fiction    275  
2  Staring unflinchingly into the abyss of slaver...  fiction    275  
3  Staring unflinchingly into the abyss of slaver...  fiction    275  
4  Staring unflinchingly into the abyss of slaver...  fiction    275

In [5]:
# removing not usefull column
final.drop("Unnamed: 0", axis=1, inplace=True)

In [6]:
# checking null values and data types
final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 169893 entries, 0 to 169892
Data columns (total 15 columns):
 #   Column             Non-Null Count   Dtype  
---  ------             --------------   -----  
 0   user               169893 non-null  int64  
 1   age                115063 non-null  float64
 2   country_2          169893 non-null  object 
 3   isbn               169893 non-null  object 
 4   rating             169893 non-null  int64  
 5   rating_count       169893 non-null  int64  
 6   avg_rating         169893 non-null  float64
 7   reaction_index     169893 non-null  float64
 8   title              169893 non-null  object 
 9   author             169893 non-null  object 
 10  median_age_raters  169789 non-null  float64
 11  title_api          169893 non-null  object 
 12  description        168621 non-null  object 
 13  category           169893 non-null  object 
 14  pages              169893 non-null  int64  
dtypes: float64(4), int64(4), object(7)
memory usage: 19

In [10]:
# correction of vague category fiction for selected author
final.loc[final['author']=='orson scott card', 'category']='scifi'

In [11]:
# saving file before normalization of variables for later use
final.to_csv(r"C:\Users\kamil\OneDrive\Plocha\Projects\books\final_result.csv")

In [12]:
# checking dataset to look for numeric values in need for normalization
final.head(2)

user   age country_2        isbn  rating  rating_count  avg_rating  \
0     9   NaN       usa  0452264464       6            79    7.772152   
1  3373  30.0       usa  0452264464      10            79    7.772152   

   reaction_index                                 title         author  \
0        0.438889  beloved (plume contemporary fiction)  toni morrison   
1        0.438889  beloved (plume contemporary fiction)  toni morrison   

   median_age_raters title_api  \
0               34.0   beloved   
1               34.0   beloved   

                                         description category  pages  
0  Staring unflinchingly into the abyss of slaver...  fiction    275  
1  Staring unflinchingly into the abyss of slaver...  fiction    275

In [13]:
# printing column name for easier copypaste in next step
final.columns

Index(['user', 'age', 'country_2', 'isbn', 'rating', 'rating_count',
       'avg_rating', 'reaction_index', 'title', 'author', 'median_age_raters',
       'title_api', 'description', 'category', 'pages'],
      dtype='object')

In [14]:
# normalization of numeric variables on scale 0 to 1
sc = preprocessing.MinMaxScaler()
final[['rating_count', 'avg_rating','pages', 'median_age_raters' ]] = sc.fit_transform(final[['rating_count', 
                                                                                              'avg_rating', 'pages', 
                                                                                              'median_age_raters']])

In [15]:
# removing columns not needed for recommender system (mainly categorical variables)
final = final.drop(columns=['user', 'age', 'country_2', 'isbn', 'rating', 'title_api', 'description'])

In [16]:
# removing duplicates for future index of dataframe
final.drop_duplicates(subset=['title'], keep='first', inplace=True)

In [17]:
# checking for null values
final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10587 entries, 0 to 169888
Data columns (total 8 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   rating_count       10587 non-null  float64
 1   avg_rating         10587 non-null  float64
 2   reaction_index     10587 non-null  float64
 3   title              10587 non-null  object 
 4   author             10587 non-null  object 
 5   median_age_raters  10574 non-null  float64
 6   category           10587 non-null  object 
 7   pages              10587 non-null  float64
dtypes: float64(5), object(3)
memory usage: 744.4+ KB


In [18]:
# looking on null value from median_age_rates
final.loc[final.median_age_raters == 0]

rating_count  avg_rating  reaction_index  \
98742      0.001425    0.666667        0.666667   

                                        title           author  \
98742  bears on wheels (bright & early books)  stan berenstain   

       median_age_raters                category     pages  
98742                0.0  books for young adults  0.023923

In [19]:
# removing null value from median_age_rates
final = final[final.median_age_raters != 0.0]

In [20]:
# new index
final.set_index('title', inplace = True)

In [21]:
# checking NaN values in dataframe
final.isna().sum()

rating_count          0
avg_rating            0
reaction_index        0
author                0
median_age_raters    13
category              0
pages                 0
dtype: int64

In [22]:
# removing NaN values
final = final.dropna()

In [23]:
final.to_csv(r"C:\Users\kamil\OneDrive\Plocha\Projects\books\final_clean.csv")

In [24]:
# creating dummies for categorical variables
dummies = pd.get_dummies(final, columns=['author', 'category'], drop_first=True)

In [25]:
# checking result of previous step
dummies.head(3)

rating_count  avg_rating  \
title                                                            
beloved (plume contemporary fiction)      0.105413    0.681736   
airframe                                  0.105413    0.636528   
death in the clouds                       0.001425    0.809524   

                                      reaction_index  median_age_raters  \
title                                                                     
beloved (plume contemporary fiction)        0.438889           0.351724   
airframe                                    0.381643           0.331034   
death in the clouds                         0.352941           0.379310   

                                         pages  \
title                                            
beloved (plume contemporary fiction)  0.187970   
airframe                              0.294600   
death in the clouds                   0.155844   

                                      author_a c bhaktivedanta swami prabhupada et al   \
title                                                                                    
beloved (plume contemporary fiction)                                                 0   
airframe                                                                             0   
death in the clouds                                                                  0   

                                      author_a c crispin  author_a c doyle  \
title                                                                        
beloved (plume contemporary fiction)                   0                 0   
airframe                                               0                 0   
death in the clouds                                    0                 0   

                                      author_a j holt  author_a l alexander  \
title                                                                         
beloved (plume contemporary fiction)                0                     0   
airframe                                            0                     0   
death in the clouds                                 0                     0   

                                      author_a m homes  \
title                                                    
beloved (plume contemporary fiction)                 0   
airframe                                             0   
death in the clouds                                  0   

                                      author_a manette ansay  \
title                                                          
beloved (plume contemporary fiction)                       0   
airframe                                                   0   
death in the clouds                                        0   

                                      author_a n roquelaure  \
title                                                         
beloved (plume contemporary fiction)                      0   
airframe                                                  0   
death in the clouds                                       0   

                                      author_a s  byatt  author_a s byatt  \
title                                                                       
beloved (plume contemporary fiction)                  0                 0   
airframe                                              0                 0   
death in the clouds                                   0                 0   

                                      author_a sewell  author_a verghese  \
title                                                                      
beloved (plume contemporary fiction)                0                  0   
airframe                                            0                  0   
death in the clouds                                 0                  0   

                                      author_aaron allston  \
title                                                        
beloved (plume contempo

In [26]:
#setting up the recommender 
recommender = cosine_similarity(dummies.iloc[:,:])

In [27]:
# checking shape of newly creted dataframe
recommender.shape

(10573, 10573)

In [28]:
#creating a dataframe to bring the title names back into view
recommender_df = pd.DataFrame(recommender, columns=dummies.index, index=dummies.index)
recommender_df.head(3)

title                                 beloved (plume contemporary fiction)  \
title                                                                        
beloved (plume contemporary fiction)                              1.000000   
airframe                                                          0.638937   
death in the clouds                                               0.647568   

title                                 airframe  death in the clouds  \
title                                                                 
beloved (plume contemporary fiction)  0.638937             0.647568   
airframe                              1.000000             0.638801   
death in the clouds                   0.638801             1.000000   

title                                 bant/spec.last of the breed  \
title                                                               
beloved (plume contemporary fiction)                     0.656547   
airframe                                                 0.648541   
death in the clouds                                      0.660000   

title                                 piercing the darkness   prophet  \
title                                                                   
beloved (plume contemporary fiction)               0.653542  0.622040   
airframe                                           0.649154  0.622060   
death in the clouds                                0.661192  0.621479   

title                                 prague : a novel  to kill a mockingbird  \
title                                                                           
beloved (plume contemporary fiction)          0.629713               0.657964   
airframe                                      0.625837               0.650329   
death in the clouds                           0.623835               0.653821   

title                                 pigs in heaven  icebound  \
title                                                            
beloved (plume contemporary fiction)        0.657323  0.637862   
airframe                                    0.649831  0.635107   
death in the clouds                         0.665704  0.638195   

title                                 i'll be seeing you  \
title                                                      
beloved (plume contemporary fiction)            0.631918   
airframe                                        0.628934   
death in the clouds                             0.640527   

title                                 from the corner of his eye  \
title                                                              
beloved (plume contemporary fiction)                    0.643590   
airframe                                                0.647979   
death in the clouds                                     0.642428   

title                                 this year it will be different: and other stories  \
title                                                                                     
beloved (plume contemporary fiction)                                           0.632803   
airframe                                                                       0.627064   
death in the clouds                                                            0.638115   

title                                 the street lawyer  \
title                                                     
beloved (plume contemporary fiction)           0.641408   
airframe                                       0.640515   
death in the clouds                            0.640560   

title                                 a soldier of the great war  \
title                                                              
beloved (plume contemporary fiction)                    0.641036   
airframe                                                0.646108   
death in the clouds                                     0.648497   

title                                 lonesome dove  \
title         

In [29]:
#reading in fresh data because the original dataframe has titles as the index now
final_2 = pd.read_csv('final_clean.csv')

In [30]:
# selecting title of book that user liked
q = 'lord of the rings'

result = list(final_2[final_2['title'].str.contains(q)]['title'].head(30))
result[:10]

['the fellowship of the ring (the lord of the rings, part 1)',
 'the hobbit and the lord of the rings',
 'the lord of the rings (movie art cover)',
 'the two towers (the lord of the rings, part 2)',
 'the return of the king (the lord of the rings, part 3)',
 "the lord of the rings (leatherette collector's edition)",
 'the lord of the rings',
 "bored of the rings: a parody of j.r.r. tolkien's the lord of the rings",
 'the two towers (lord of the rings (paperback))',
 'the fellowship of the ring (lord of the rings (paperback))']

In [31]:
# selecting specific book from presented choices
i = 7

In [32]:
# looking up recommendations
rec_results = ((recommender_df[result[i-1]].sort_values(ascending=False)[1:60]).to_frame()).reset_index()
rec_results.rename(columns={rec_results.columns[1]: "similarity to selected book" }, inplace = True)

In [33]:
# reading saved dataframe to extraxt only data needed for final result shown to user
final_cl = pd.read_csv('final_result.csv', sep=',')
final_cl.drop_duplicates(subset=['title'], keep='first', inplace=True)
final_cl = final_cl[["title", "author", "description", "category", "pages"]]

In [34]:
# joining tables with recommended titles and tables with additional info
results = pd.merge(rec_results, final_cl, on='title', how='left')
results.head(10)

title  \
0            the lord of the rings (movie art cover)   
1     the two towers (the lord of the rings, part 2)   
2  the return of the king (the lord of the rings,...   
3  the lord of the rings (leatherette collector's...   
4  the fellowship of the ring (the lord of the ri...   
5                         the fellowship of the ring   
6               the hobbit and the lord of the rings   
7  the return of the king (lord of the rings (pap...   
8                                two towers rings uk   
9  the fellowship of the ring (lord of the rings ...   

   similarity to selected book         author  \
0                     0.998594  j r r tolkien   
1                     0.997880  j r r tolkien   
2                     0.996272  j r r tolkien   
3                     0.992647  j r r tolkien   
4                     0.977709  j r r tolkien   
5                     0.975807  j r r tolkien   
6                     0.974793  j r r tolkien   
7                     0.969519  j r r tolkien   
8                     0.968880  j r r tolkien   
9                     0.965846  j r r tolkien   

                                         description category  pages  
0  Presents the epic depicting the Great War of t...  fantasy   1137  
1  The second volume in J.R.R. Tolkien's epic adv...  fantasy   1137  
2  In a sleepy village in the Shire, young Frodo ...  fantasy   1137  
3  An epic fantasy, chronicling the great War of ...  fantasy   1215  
4  The first volume of a three-volume epic advent...  fantasy    527  
5  Frodo Baggins, bearer of the Ring of Power tha...  fantasy    527  
6  The War of the Rings comes to a close as Frodo...  fantasy    491  
7  For over fifty years, J.R.R. Tolkien's peerles...  fantasy    544  
8  Tolkien's invention of strange people, curious...  fantasy    442  
9  Frodo Baggins, bearer of the Ring of Power tha...  fantasy    527

In [35]:
# new variable to see how many books from certain author were recommended
results['author_book_count'] = results.groupby('author')['title'].rank(method='first')
results.head(10)

title  \
0            the lord of the rings (movie art cover)   
1     the two towers (the lord of the rings, part 2)   
2  the return of the king (the lord of the rings,...   
3  the lord of the rings (leatherette collector's...   
4  the fellowship of the ring (the lord of the ri...   
5                         the fellowship of the ring   
6               the hobbit and the lord of the rings   
7  the return of the king (lord of the rings (pap...   
8                                two towers rings uk   
9  the fellowship of the ring (lord of the rings ...   

   similarity to selected book         author  \
0                     0.998594  j r r tolkien   
1                     0.997880  j r r tolkien   
2                     0.996272  j r r tolkien   
3                     0.992647  j r r tolkien   
4                     0.977709  j r r tolkien   
5                     0.975807  j r r tolkien   
6                     0.974793  j r r tolkien   
7                     0.969519  j r r tolkien   
8                     0.968880  j r r tolkien   
9                     0.965846  j r r tolkien   

                                         description category  pages  \
0  Presents the epic depicting the Great War of t...  fantasy   1137   
1  The second volume in J.R.R. Tolkien's epic adv...  fantasy   1137   
2  In a sleepy village in the Shire, young Frodo ...  fantasy   1137   
3  An epic fantasy, chronicling the great War of ...  fantasy   1215   
4  The first volume of a three-volume epic advent...  fantasy    527   
5  Frodo Baggins, bearer of the Ring of Power tha...  fantasy    527   
6  The War of the Rings comes to a close as Frodo...  fantasy    491   
7  For over fifty years, J.R.R. Tolkien's peerles...  fantasy    544   
8  Tolkien's invention of strange people, curious...  fantasy    442   
9  Frodo Baggins, bearer of the Ring of Power tha...  fantasy    527   

   author_book_count  
0               15.0  
1               24.0  
2               18.0  
3               14.0  
4                7.0  
5                5.0  
6               11.0  
7               17.0  
8               25.0  
9                6.0

In [36]:
# setting limit of recommended number of books by one author
results = (results[results['author_book_count']<6]).head(10)

In [37]:
# more user friendly NaN
results.description = results.description.fillna("no description available")

In [38]:
# removing helper column author_book_count because we don't want a user to it
results.drop(results.columns[-1], axis=1, inplace=True)

In [39]:
# adding display option for better reading of description column
from pandas import option_context

with option_context('display.max_colwidth', 250):
    display(results)

title  \
5                                          the fellowship of the ring   
10  the book of lost tales 2 (the history of middle-earth - volume 2)   
15  the book of lost tales 1 (the history of middle-earth - volume 1)   
21                     smith of wootton major and farmer giles of ham   
24                                              poems from the hobbit   
26                  a clash of kings (a song of fire and ice, book 2)   
27                                                               maia   
29                                            the discworld companion   
30                                         dracula (penguin classics)   
31                                               circle and the cross   

    similarity to selected book             author  \
5                      0.975807      j r r tolkien   
10                     0.959466      j r r tolkien   
15                     0.957037      j r r tolkien   
21                     0.936559      j r r tolkien   
24                     0.926810      j r r tolkien   
26                     0.727903  george r r martin   
27                     0.705359      richard adams   
29                     0.695823     stephen briggs   
30                     0.692372        bram stoker   
31                     0.690046        caiseal mor   

                                                                                                                                                                                                                                                  description  \
5   Frodo Baggins, bearer of the Ring of Power that would enable the evil Sauron to destroy all that is good in Middle-earth, takes on the task of carrying the Ring to Mount Doom to oversee its destruction. A new cover features artwork from the upcom...   
10                                       The second part of the book that was Tolkien's first conception of the Middle Kingdom features the tales of Beren and Luthien, Turin and the Dragon, the Necklace of the Dwarves, and the Fall of Gondolin. Reissue.   
15          The first form of the myths and legends in Tolkien's conception of the Middle Kingdom features the adventures of Eriol, and the tales of Beren and Luthien, Turin and the dragon, the necklace of the dwarves, and the fall of Gondolin. Reissue.   
21  Two bewitching fantasies by J.R.R. Tolkien, beloved author of THE HOBBIT. In SMITH OF WOOTTON MAJOR, Tolkien explores the gift of fantasy, and what it means to the life and character of the man who receives it. And FARMER GILES OF HAM tells a del...   
24                                                                                             A perfect literary complement to Tolkien's enchanting universe features the poems and riddles contained in the Hobbit, enlivened by the author's own drawings.   
26                                                                                       A medieval fantasy on the land of the Seven Kingdoms, chronicling the intrigues of its ruling families as they jockey for power. By the author of A Game of Thrones.   
27                                                                                                                                                                                                                                   no description available   
29                 Who taught witchcraft to Granny Weatherwax? What does Death keep on his desk? This is an A-Z guide to the characters, places, flora and fauna of Terry Pratchett's fantasy planet, Discworld, with sketches and maps of the key locations.   
30  Told in journal fragments that cannot provide any reliable perspective, Dracula is at the same time Romantic and modern. It unfolds the story of a Transylvanian Don Juan, the aristocratic vampire Count Dracula, who preys on damsels, and of the mi...   
31                                                                                             

In [40]:
# all previous steps condensed into class recommend_book
class recommend_book:
    def book_select(self):
        q = input("Write name of the book did you like. We will try to find similar books to that one: ")
        self.result = list(final_2[final_2['title'].str.contains(q)]['title'].head(10))
        for i, value in enumerate(self.result):
            print(i+1, value)
        if self.result == []:
            print("Sorry, the book you look for is not in our database. Please try another one.")
            q = input("Write name of the book did you like. We will try to find similar books to that one: ")
            self.result = list(final_2[final_2['title'].str.contains(q)]['title'].head(10))
            for i, value in enumerate(self.result):
                print(i+1, value)

    def show_results(self):
        i = int(input("Write number of your selected book from options above: "))    
        rec_results = ((recommender_df[self.result[i-1]].sort_values(ascending=False)[1:60]).to_frame()).reset_index()
        rec_results.rename(columns={rec_results.columns[1]: "similarity to selected book" }, inplace = True)
        final_cl = pd.read_csv('final_result.csv', sep=',')
        final_cl.drop_duplicates(subset=['title'], keep='first', inplace=True)
        final_cl = final_cl[["title", "author", "description", "category", "pages"]]
        results = pd.merge(rec_results, final_cl, on='title', how='left')
        results['author_book_count'] = results.groupby('author')['title'].rank(method='first')
        results = (results[results['author_book_count']<6]).head(10)
        results.description = results.description.fillna("no description available")
        results.drop(results.columns[-1], axis=1, inplace=True)
        with option_context('display.max_colwidth', 250):
            display(results)

In [41]:
# calling functions from new class for ender
class_instance = recommend_book()
class_instance.book_select()
class_instance.show_results()

Write name of the book did you like. We will try to find similar books to that one: ender
1 shadow of the hegemon (ender wiggins saga (paperback))
2 ender's game (ender wiggins saga (paperback))
3 surrender
4 ender's shadow
5 shadow of the hegemon (ender wiggins saga (hardcover))
6 the great pretender
7 tender stranger (harlequin historical, no. 456)
8 tender at the bone: growing up at the table
9 tender is the night
10 ender's game
Write number of your selected book from options above: 10


title  \
0                                             enchantment   
2         alvin journeyman (tales of alvin maker, book 4)   
12          ender's game (ender wiggins saga (paperback))   
16                                         ender's shadow   
18  children of the mind (ender wiggins saga (paperback))   
31                            another roadside attraction   
32          god emperor of dune (dune chronicles, book 4)   
33                                           sixth column   
34             dune (dune chronicles (berkley paperback))   
35                            jaran (daw book collectors)   

    similarity to selected book             author  \
0                      0.998341   orson scott card   
2                      0.997621   orson scott card   
12                     0.994782   orson scott card   
16                     0.994140   orson scott card   
18                     0.993545   orson scott card   
31                     0.673404            robbins   
32                     0.671521      frank herbert   
33                     0.671028  robert a heinlein   
34                     0.669275      frank herbert   
35                     0.668077       kate elliott   

                                                                                                                                                                                                                                                  description  \
0            One of the most popular contemporary authors of science fiction follows one man from ninthcentury Russia to presentday America as he struggles to rescue a princess and her kingdom, find true love, and overcome the blackest of evil. Repirnt.   
2                       Alvin Miller, a gifted seventh son of a seventh son, utilizes his skills as a Maker to help create a brighter future for America, but his task is further challenged by his ancient enemy, the Unmaker, who plots to end Alvin's life   
12  Winner of the Hugo and Nebula Awards In order to develop a secure defense against a hostile alien race's next attack, government agencies breed child geniuses and train them as soldiers. A brilliant young boy, Andrew "Ender" Wiggin lives with his...   
16  The novel that launched the bestselling Ender's Shadow series. The human race is at War with the "Buggers," an insect-like alien race. As Earth prepares to defend itself from total destruction at the hands of an inscrutable enemy, all focus is on...   
18            In the conclusion of the Ender saga, Ender Wiggin confronts his ultimate challenge when his adopted world, Lusitania, is threatened by his old planet-destroying weapon, and his ally, Jane, is about to be killed off by the Starways Congress   
31  What if the Second Coming didn't quite come off as advertised? What if "the Corpse" on display in that funky roadside zoo is really who they say it is--what does that portent for the future of western civilization? And what if a young clairvoyant...   
32                                           Centuries have passed on Dune, and the planet is green with life. Leto, the son of Dune's savior, is still alive but far from human, and the fate of all humanity hangs on his awesome sacrifice... --Publisher.   
33                          America has become the last of the Free Nations to fall. Though scattered resistance flares throughout the continent, the only real hope resides in a mountain redoubt where six men work in secret on a plan to rock the planet.   
34                                                    Paul Atreides moves with his family to the planet Dune and is forced into exile when his father's government is overthrown. The first book in the series. Copyright Â© Libri GmbH. All rights reserved.   
35  The brilliant first novel of an author destined to become an important new voice in science fiction. A young woman comes of age in an alien world where she is both a player and a pawn in an interstellar game of 